In [1]:
#%%capture

# install the latest version of kaggle_environments
#!pip install --upgrade kaggle_environments

In [2]:
# This package will work automatically on Kaggle's notebooks as their environment already have
# all required dependencies, but you can find on the discussion section tutorials about installing the 
# Kaggle environment in your machine in order to develop and test there your agents
from kaggle_environments import make
env = make("kore_fleets", debug=True)
print(env.name, env.version)

kore_fleets 1.2.0


In [3]:
%%writefile ./agents/baseline_agent.py
# This line creates the "agent.py" file that you need to download and submit to the competition page
# Otherwise, you can copy and paste this entire cell (without the first line), save it into a plain text file and name it "baseline_agent.py"

# Creating a besline strategy from the tutorial notebooks slightly improved with some extra conditions
# Original baseline: https://github.com/Kaggle/kaggle-environments/blob/master/kaggle_environments/envs/kore_fleets/starter_bots/python/main.py

from kaggle_environments.envs.kore_fleets.helpers import *
from random import randint

def agent(obs, config):
    board = Board(obs, config)

    me = board.current_player
    turn = board.step
    spawn_cost = board.configuration.spawn_cost
    kore_left = me.kore

    for shipyard in me.shipyards:
        
        if shipyard.ship_count > (10 + int(turn/8)):
            n_ships = 2 + int(turn/10)
            direction = Direction.from_index(randint(1,2))
            if n_ships > 21:
                lateral_dev = randint(1,9)
                if lateral_dev == 2:        # avoiding enemy shipyard
                    lateral_dev = 0
                flight_plan = [f'E{lateral_dev}N9W{lateral_dev}N', 
                               f'W{lateral_dev}N9E{lateral_dev}N'][randint(0,1)] 
            else:
                flight_plan = Direction.from_index(randint(0,1)).to_char()
            action = ShipyardAction.launch_fleet_with_flight_plan(n_ships, flight_plan)
            shipyard.next_action = action
        
        elif kore_left > spawn_cost * shipyard.max_spawn:
            if turn > 200:
                n_ships = int(shipyard.max_spawn / 2)
            else:
                n_ships = shipyard.max_spawn
            action = ShipyardAction.spawn_ships(n_ships)
            shipyard.next_action = action
            kore_left -= spawn_cost * n_ships
        
        elif kore_left > spawn_cost:
            action = ShipyardAction.spawn_ships(1)
            shipyard.next_action = action
            kore_left -= spawn_cost

    return me.next_actions

Writing ./baseline_agent.py


In [5]:
# This allows to display a 2D dynamic visualization of a game with 4 agents to debugg and see the strategy locally before submitting it

#agent_path = "/kaggle/working/agent.py"
agent_path = "./agents/baseline_agent.py"
env.run([agent_path, agent_path, agent_path, agent_path])
env.render(mode="ipython", width=1000, height=800)

In [6]:
# Testing the fleet plan length rule as a function of the fleet's number of ships

import numpy as np
from math import floor

flt_plan_l = lambda x: floor(2 * np.log(x)) + 1

{ships: flt_plan_l(ships) for ships in range(2, 101) if flt_plan_l(ships) != flt_plan_l(ships-1)}

{2: 2, 3: 3, 5: 4, 8: 5, 13: 6, 21: 7, 34: 8, 55: 9, 91: 10}

In [ ]:
!ls ./

In [9]:
mining_f = lambda num_ships: np.log(num_ships) / 20

In [11]:
mining_f(21)

0.15222612188617116

In [ ]:
spawned_ships = lambda turns: turns**2 + 1